In [193]:
# Import Packages & Libraries

import os

# Analysis Libraries

import numpy as np # For working with Arrays
import pandas as pd # Data Manipulation
import geopandas as gpd # Spatial Data Manipulation
from scipy import interpolate as interp # # different interpolators
import rasterio # Rasters
from rasterio.transform import Affine

# Visualization Libraries

import folium # Interactive Leaflet.js mapping 
from folium import features

import matplotlib.pyplot as plt # Basic Plotting
from matplotlib import colors # For colormap creation 
from matplotlib import cm
import math
plt.style.use('ggplot') # 
import seaborn as sns # Statistical Plotting
import contextily # Base Map Visualization

# Interaction

from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
import datetime # Time

# Silence Warnings

import warnings
warnings.filterwarnings('ignore')

## Definitions

In [30]:
focus_pollutants = ['PM2.5 Primary', 'Sulfur Dioxide', 'Nitrogen Oxides',
              'Carbon Monoxide', 'Volatile Organic Compounds', 'Lead', '2,3,7,8-Tetrachlorodibenzo-P-Dioxin']

temp = data_dict['emissions']
emissions_year = max(temp.YEAR) # Get the most current year

# Join with facilities

facs_w_data = data_dict['facs'].copy()

for pollutant in focus_pollutants:
    # temp = temp[(temp.YEAR == emissions_year) & (temp.POLLUTANT.isin(focus_pollutants))] # Select by pollutant and year
    
    # Current
    
    select = temp[(temp.YEAR == emissions_year) 
                & (temp.POLLUTANT == pollutant)][['FACILITY_ID', 'LBS_EMITTED']
                                                ].rename(columns={'LBS_EMITTED':pollutant + ' CURRENT'})

    facs_w_data = pd.merge(left=facs_w_data, right=select, 
                           left_on = 'FACILITY_ID', right_on = 'FACILITY_ID',
                           how = 'left'
                          )

    # 10 year cumulative

    select = temp[(temp.YEAR > emissions_year-10) 
            & (temp.POLLUTANT == pollutant)].groupby(['FACILITY_ID', 'POLLUTANT']).sum().reset_index()[['FACILITY_ID', 'LBS_EMITTED']
                                                ].rename(columns={'LBS_EMITTED':pollutant + ' 10YEAR'})

    facs_w_data = pd.merge(left=facs_w_data, right=select, 
                           left_on = 'FACILITY_ID', right_on = 'FACILITY_ID',
                           how = 'left'
                          )

In [75]:
def prep_emissions(emissions_df, facilities_df, focus_pollutants, focus_pollutants_nameDict):
    

    temp = emissions_df
    emissions_year = max(temp.YEAR) # Get the most current year
    
    # Join with facilities
    
    facs_w_data = facilities_df.copy()
    
    for pollutant in focus_pollutants:
        # temp = temp[(temp.YEAR == emissions_year) & (temp.POLLUTANT.isin(focus_pollutants))] # Select by pollutant and year
        
        # Current
        
        select = temp[(temp.YEAR == emissions_year) 
                    & (temp.POLLUTANT == pollutant)][['FACILITY_ID', 'LBS_EMITTED']
                                                    ].rename(columns={'LBS_EMITTED':focus_pollutants_nameDict[pollutant] + '_CURRENT'})
    
        facs_w_data = pd.merge(left=facs_w_data, right=select, 
                               left_on = 'FACILITY_ID', right_on = 'FACILITY_ID',
                               how = 'left'
                              )
    
        # 10 year cumulative
    
        select = temp[(temp.YEAR > emissions_year-10) 
                & (temp.POLLUTANT == pollutant)].groupby(['FACILITY_ID', 'POLLUTANT']).sum().reset_index()[['FACILITY_ID', 'LBS_EMITTED']
                                                    ].rename(columns={'LBS_EMITTED':focus_pollutants_nameDict[pollutant] + '_10YEAR'})
    
        facs_w_data = pd.merge(left=facs_w_data, right=select, 
                               left_on = 'FACILITY_ID', right_on = 'FACILITY_ID',
                               how = 'left'
                              )
    
    
        
    return facs_w_data.fillna(0)
    

## Load Data

In [99]:
datapath = os.path.join('..', '..', 'Data')

## Storage for datasets

data_dict = {}

# Boundary - From MetroCouncil 2010 CTU boundaries

path = os.path.join(datapath, 'mpls_boundary.geojson')
data_dict['mpls'] = gpd.read_file(path)

# Traffic

path = os.path.join(datapath, 'mpls_aadt.geojson')
data_dict['aadt'] = gpd.read_file(path)

# Emissions
## Facilitites
path = os.path.join(datapath, 'mpca_facilities.geojson')
data_dict['facs'] = gpd.clip(gpd.read_file(path), data_dict['mpls'].buffer(1000))
## Emissions
path = os.path.join(datapath, 'MPCA_Permitted_Emissions.csv')
data_dict['emissions'] = pd.read_csv(path)

# Health

path = os.path.join(datapath, 'mpls_health.geojson')
data_dict['health'] = gpd.read_file(path)

# Demographics

path = os.path.join(datapath, 'mpls_demographics2019.geojson')
data_dict['demo'] = gpd.read_file(path)

# PurpleAir Stations

path = os.path.join(datapath, 'PurpleAir_Stations.geojson')
stations = gpd.read_file(path)
stations['sensor_index'] = stations.sensor_index.astype(int)
data_dict['stations'] = stations

# PM2.5 Readings and Daily Summaries - From Purple Air

# Results are in micrograms/meter^3
# Mn Health benchmarks found at: https://www.health.state.mn.us/communities/environment/risk/guidance/air/table.html

path = os.path.join(datapath, 'daily_summaries.csv')
daily_sums = pd.read_csv(path)
daily_sums['date'] = pd.to_datetime(daily_sums.date)
data_dict['daily_sums'] = daily_sums

# Spikes

path = os.path.join(datapath, 'all_spikes.csv')
spikes = pd.read_csv(path)
spikes['timestamp'] = pd.to_datetime(spikes.timestamp)
data_dict['spikes'] = spikes

In [136]:
# Prep Data

## Traffic

temp = data_dict['aadt'][['SEQUENCE_N', 'ROUTE_LABE', 'CURRENT_VO', 'geometry']] # Select Columns
max_aadtvol = max(temp.CURRENT_VO)
aadt_webmap = temp[temp['CURRENT_VO'] > 10000] # Select high-volume Roads

# Emissions

focus_pollutants = ['PM2.5 Primary', 'Sulfur Dioxide', 'Nitrogen Oxides',
              'Carbon Monoxide', 'Volatile Organic Compounds', 'Lead']#, '2,3,7,8-Tetrachlorodibenzo-P-Dioxin']

focus_pollutants_nameDict = {'PM2.5 Primary':'PM2.5',
                             'Sulfur Dioxide':'SO2',
                             'Nitrogen Oxides':'NOx',
                              'Carbon Monoxide':'CO',
                             'Volatile Organic Compounds':'VOC', 
                             'Lead':'Lead', 
                             #'2,3,7,8-Tetrachlorodibenzo-P-Dioxin':'Dioxin'
                            }

emissions_year = max(data_dict['emissions'].YEAR) # Get the most current year
emissions_webmap = prep_emissions(data_dict['emissions'], data_dict['facs'], 
                                  focus_pollutants, focus_pollutants_nameDict)

# Focus & Merge Health/Demographic Data

tracts_webmap = gpd.GeoDataFrame(pd.merge(left=data_dict['health'].iloc[:,:-1], 
                                          right=data_dict['demo'], on='GEOID'))

focus_health_nameDict = {'STROKE':'Stroke among adults aged >=18 years',
                               'CASTHMA':'Current asthma among adults aged >=18 years',
                  'ACCESS2':'Current lack of health insurance among adults aged 18-64 years',
                  'KIDNEY':'Chronic kidney disease among adults aged >=18 years', 
                  'CHD':'Coronary heart disease among adults aged >=18 years', 
                  'COPD':'Chronic obstructive pulmonary disease among adults aged >=18 years'}

tracts_webmap=tracts_webmap.rename(columns=focus_health_nameDict)

## Define Visualizations

In [214]:
### Tracts Style

def style_tracts(feature, hexcodes):

    bin_n = feature['properties']['bin']

    return {'fillColor': hexcodes[bin_n], 
                            'color':'#000000', 
                            'fillOpacity': 0.5, 
                            'weight': 1.
           }
    

In [121]:
### AADT style

def style_aadt(feature, maxvol):
    '''Set Thickness/color of streets to be proportional to traffic volume'''
    
    volume = feature['properties']['CURRENT_VO']

    weight = 10*volume/maxvol
    color = "#8a4d1a"

    return {
        "weight": weight,
        "color": color
    }

In [237]:
### Emissions Popup

def emissions_popup_html(point, pollutants, decimals):
    '''Creates a popup with basic info on an industrial polluter'''

    left_col_color = "#627c6a"
    right_col_color = "#bccdb9"
    
    html = """<!DOCTYPE html>
<html>

<head>
<h4 style="margin-bottom:10"; width="200px">{} ({})</h4>""".format(point.FACILITY_NAME, point.LAST_REPORT) + """

</head>
    <table style="height: 100px; width: 250px; text-align: right;">
<tbody>
<tr>
<td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;">Industry Type:</span></td>
<td style="width: 100px;background-color: """+ right_col_color +""";">{}</td>""".format(point.INDUSTRY_TYPE) + """
</tr>
<tr>
<td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;">NAICS code:</span></td>
<td style="width: 100px;background-color: """+ right_col_color +""";">{}</td>""".format(point.NAICS_CODE) + """
</tr>
"""
    for pollutant in pollutants:
        html = html + """<tr>
<td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;">{} Pounds Emitted:
""".format(pollutant) + """</span></td>
<td style="width: 100px;background-color: """+ right_col_color +""";">{0:,.{1}f}</td>
""".format(point[pollutant+'_CURRENT'], decimals) + """
</tr>
"""

    html = html + """</tbody>
</table>
</html>
"""
    return html

In [240]:
def plot_emitter(point, feature_group, pollutant, maxvol, pollutants):

    '''Set Thickness/color of facilities to be proportional to emissions volume'''
    
    volume = point[pollutant+'_CURRENT']

    if volume < .01*maxvol:
        pass
    else:
        weight = 10*volume/maxvol
        color = "#8a4d1a"
    
        popup = emissions_popup_html(point, pollutants, 1)
            
        folium.Circle(location=[point.geometry.y,point.geometry.x],
                           weight = weight,
                           color = color,
                           fill = True,
                           popup = popup
                           ).add_to(feature_group)    

## Make the map!

In [247]:
# Make a basic folium map

m = folium.Map(location=[44.986656, -93.258133],
               zoom_start=12,
               tiles = 'cartodbpositron')

# Add Minneapolis boundary

folium.GeoJson(data_dict['mpls'],
               style_function = lambda feature: {'color':'#000000', # Border color
                                                'fillOpacity' : '0'}, # Fill transparency
               name="Minneapolis Boundary", # Layer's Name
               control = False # Can you toggle in layer control?
              ).add_to(m)

# Add Tracts 

# Setting style for popups
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

focus_columns = list(tracts_webmap.columns[1:-1])
health_cols = list(data_dict['health'].rename(columns=focus_health_nameDict).columns[1:-1])
dem_cols = list(data_dict['demo'].columns[1:-1])

for column in focus_columns:

    if column in health_cols:
        popup_cols = dem_cols
    elif column in dem_cols:
        popup_cols = health_cols
    else:
        popup_cols = []


    maxval = tracts_webmap[column].max()

    # Determine colormap
    
    n_breaks = 4
    
    cmap_base = cm.get_cmap('BuPu', 256)
    my_color_vals = cmap_base(np.linspace(0, 1, n_breaks))     
    my_hexcodes = [colors.rgb2hex(rgba) for rgba in my_color_vals]

    # Get bins
    temp_df = tracts_webmap.copy()
    temp_df['bin'] = pd.cut(temp_df[column], n_breaks, labels = False)

    geoj = folium.GeoJson(temp_df,
               style_function = lambda feature: style_tracts(feature, my_hexcodes), 
               name = column,
               highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1},
               show = False # Does this appear in default of map
              )
    folium.features.GeoJsonPopup(fields=[column]+popup_cols, labels=True).add_to(geoj)
    geoj.add_to(m)

# Add traffic (0.2 mb)

aadt_webmap['Current Volume (Vehicles/Day)'] = aadt_webmap['CURRENT_VO'].apply(lambda x: '{0:,}'.format(int(x)))

geoj = folium.GeoJson(aadt_webmap,
               style_function = lambda feature: style_aadt(feature, max_aadtvol), 
                      highlight_function=lambda x: {'fillColor': '#f72020', 
                                'color':'#f72020', 
                                'weight': 3},
               name = 'Annual Average Daily Traffic',
               show = False # Does this appear in default of map
              )
folium.features.GeoJsonTooltip(fields=['Current Volume (Vehicles/Day)'],
                               labels=True).add_to(geoj)
geoj.add_to(m)

# Add Emissions (0.4 mb)

for pollutant in list(focus_pollutants_nameDict.values()): # By Pollutant

    layername = pollutant + ' Emitters'

    focus_df = emissions_webmap[emissions_webmap[pollutant+'_CURRENT']>0].to_crs('EPSG:4326')

    max_pollutant = focus_df[pollutant+'_CURRENT'].max()

    feature_group = folium.FeatureGroup(name = layername,
                                           show = False) # Create Feature Group
    focus_df.apply(lambda x: plot_emitter(x, feature_group, pollutant, max_pollutant,
                                          list(focus_pollutants_nameDict.values())),
                   axis = 1) # Add to group
    
    m.add_child(feature_group)

        

m.add_child(folium.map.LayerControl())

m

In [242]:
# Save Map

m.save(os.path.join('.', 'MVP.html'))